### 中醫醫案症狀詞抽取
- model: CRF
- 主症與兼症合併
- 詞位標注: OSBIE
- 671個詞沒有完全對應(皆標為O)
- postag使用nltk

In [1]:
import json
import nltk
import numpy as np

In [2]:
def getTagListWithString(str):
    list1 = []
    str = str.replace('，',' ')
    str = str.replace('、',' ')
    str = str.replace(',',' ')
    str_list = str.split(" ")
    
    for s in str_list:
        s = s.strip()
        if len(s) > 0:
            list1.append(s)
    
    #list2 = list(filter(None, second_list))

    return list1
    

In [3]:
def getLabelWithWordIndex(i,ne_index_list):
    for (ne_idx,ne_len) in ne_index_list: 
        if i == ne_idx:
            return "B-S"
        elif i > ne_idx and i < (ne_idx + ne_len - 1):
            return "I-S"
        elif i == (ne_idx + ne_len - 1):
            return "E-S"
            
    return "O"

In [13]:
filename = "case_summary.csv"
with open(filename) as f:
    lines = f.readlines()

docs = []
c = 0
t = 0
for idx,line in enumerate(lines):
    cols = line.strip().split(",")
    case_content = cols[2].replace(" ","")
    summary_str = cols[3].strip()
    
    if idx == 0 or len(summary_str) == 0 :
        continue
        
    #處理每個doc的summary(主症和兼症)
    print(summary_str)
    summary_str = summary_str.strip('"')
    summary_str = summary_str.replace('""','"')
    summary_str = summary_str.replace('#',',')
    
    #print(summary_str)
        
    summary_json = json.loads(summary_str)
        
    keys = summary_json.keys()
    if "main" in keys:
        main = summary_json["main"]
        main_list = getTagListWithString(main)
        #print(main_list)
    if "second" in keys:
        second = summary_json["second"]
        second_list = getTagListWithString(second)
        #print(second_list)
        
    if len(second_list) > 0:
        main_list.extend(second_list)
    
    t += len(main_list)
        
    ne_index_list = []
    for ne in main_list:
        ne_idx = case_content.find(ne)
        if ne_idx != -1 :
            ne_index_list.append((ne_idx,len(ne)))
    
    '''
    if len(main_list) != len(ne_index_list):
        c += 1
        #print(case_content)
        print(main_list)
        for i,l in ne_index_list:
            print(case_content[i])
        print("------------")
    '''
    
    texts = []
    for i,w in enumerate(case_content):
        label = getLabelWithWordIndex(i,ne_index_list)
        texts.append((w,label))
        
    docs.append(texts)

print(t)
print(c)

"{""main"": ""寒热不适，发热又需披衣，汗透衣服""# ""pulse"": ""脉虚大而迟""# ""recipe"": {""raw"": """"# ""memo"": """"# ""title"": ""桂枝汤""}# ""second"": """"# ""tongue"": ""苔薄黄""# ""chinese"": ""发热""# ""therapy"": """"# ""western"": """"# ""dialectical"": """"}"
"{""main"": ""咳吐稀痰   呼吸气上涌喘息""# ""pulse"": """"# ""recipe"": {""raw"": ""桂枝 12 g\r\n芍药 30 g\r\n炙甘草 10 g\r\n生姜 10 g\r\n大枣 25 g\r\n厚朴 30 g\r\n杏仁 20 g""# ""item"": [{""name"": ""桂枝""# ""unit"": ""g""# ""amount"": ""12""}# {""name"": ""芍药""# ""unit"": ""g""# ""amount"": ""30""}# {""name"": ""炙甘草""# ""unit"": ""g""# ""amount"": ""10""}# {""name"": ""生姜""# ""unit"": ""g""# ""amount"": ""10""}# {""name"": ""大枣""# ""unit"": ""g""# ""amount"": ""25""}# {""name"": ""厚朴""# ""unit"": ""g""# ""amount"": ""30""}# {""name"": ""杏仁""# ""unit"": ""g""# ""amount"": ""20""}]# ""memo"": """"# ""type"": ""soup""# ""title"": ""桂枝加厚朴杏子汤""}# ""second"": ""恶风 阴囊湿冷""# ""tongue"": """"# ""chinese"": """"# ""therapy"": """"# ""western"": ""肺炎""# ""dialectical"": ""风寒犯肺，肺气上逆""

"{""main"": ""停经三月余，纳滞""# ""pulse"": ""脉滑""# ""recipe"": {""raw"": ""党参 12 克\r\n砂仁壳 2.4 克\r\n白术 9 克\r\n石决明 12 克\r\n苏梗 6 克\r\n黄芩 6 克\r\n淡竹茹 9 克\r\n姜半夏 6 克\r\n陈皮 4.5 克""# ""item"": [{""name"": ""党参""# ""unit"": ""克""# ""amount"": ""12""}# {""name"": ""砂仁壳""# ""unit"": ""克""# ""amount"": ""2.4""}# {""name"": ""白术""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""石决明""# ""unit"": ""克""# ""amount"": ""12""}# {""name"": ""苏梗""# ""unit"": ""克""# ""amount"": ""6""}# {""name"": ""黄芩""# ""unit"": ""克""# ""amount"": ""6""}# {""name"": ""淡竹茹""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""姜半夏""# ""unit"": ""克""# ""amount"": ""6""}# {""name"": ""陈皮""# ""unit"": ""克""# ""amount"": ""4.5""}]# ""memo"": """"# ""type"": ""soup""# ""title"": ""顺肝益气汤""}# ""second"": ""尿意频，时有呕泛，形寒，纳滞""# ""tongue"": """"# ""chinese"": ""恶阻""# ""therapy"": ""安养和中，和胃、降逆、止呕、安胎""# ""western"": """"# ""dialectical"": ""中虚胃逆""}"
"{""main"": ""胁肋胀痛，肋下癥块，腹水""# ""pulse"": ""脉沉弦细无力""# ""recipe"": {""raw"": """"# ""memo"": ""

"{""main"": ""谵语，咳嗽，咯痰黏黄欠爽，夹有铁诱色""# ""pulse"": ""脉滑数""# ""recipe"": {""raw"": ""水炙 3 g\r\n甘草 3 g\r\n光杏仁 9 g\r\n黑山栀 9 g\r\n鱼腥草 18 g\r\n生石膏 30 g\r\n鲜芦根 30 g\r\n广郁金 6 g\r\n知母 6 g\r\n炒黄芩 6 g\r\n炙桑皮 9 g\r\n银花 9 g\r\n白茅根 15 g""# ""item"": [{""name"": ""水炙""# ""unit"": ""g""# ""amount"": ""3""}# {""name"": ""甘草""# ""unit"": ""g""# ""amount"": ""3""}# {""name"": ""光杏仁""# ""unit"": ""g""# ""amount"": ""9""}# {""name"": ""黑山栀""# ""unit"": ""g""# ""amount"": ""9""}# {""name"": ""鱼腥草""# ""unit"": ""g""# ""amount"": ""18""}# {""name"": ""生石膏""# ""unit"": ""g""# ""amount"": ""30""}# {""name"": ""鲜芦根""# ""unit"": ""g""# ""amount"": ""30""}# {""name"": ""广郁金""# ""unit"": ""g""# ""amount"": ""6""}# {""name"": ""知母""# ""unit"": ""g""# ""amount"": ""6""}# {""name"": ""炒黄芩""# ""unit"": ""g""# ""amount"": ""6""}# {""name"": ""炙桑皮""# ""unit"": ""g""# ""amount"": ""9""}# {""name"": ""银花""# ""unit"": ""g""# ""amount"": ""9""}# {""name"": ""白茅根""# ""unit"": ""g""# ""amount"": ""15""}]# ""memo"": """"# ""type""

"{""main"": ""右胁部疼痛，全身黄中度黄染，面色黄而晦暗无华，满月脸，唇红""# ""pulse"": ""脉滑缓""# ""recipe"": {""raw"": ""金钱草 30 克\r\n黄皮树寄生 30 克\r\n田基黄 24 克\r\n土茵陈 24 克\r\n麦芽 24 克\r\n郁金 9 克\r\n云茯苓 15 克\r\n白术 15 克\r\n甘草 6 克""# ""item"": [{""name"": ""金钱草""# ""unit"": ""克""# ""amount"": ""30""}# {""name"": ""黄皮树寄生""# ""unit"": ""克""# ""amount"": ""30""}# {""name"": ""田基黄""# ""unit"": ""克""# ""amount"": ""24""}# {""name"": ""土茵陈""# ""unit"": ""克""# ""amount"": ""24""}# {""name"": ""麦芽""# ""unit"": ""克""# ""amount"": ""24""}# {""name"": ""郁金""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""云茯苓""# ""unit"": ""克""# ""amount"": ""15""}# {""name"": ""白术""# ""unit"": ""克""# ""amount"": ""15""}# {""name"": ""甘草""# ""unit"": ""克""# ""amount"": ""6""}]# ""memo"": """"# ""type"": ""soup""# ""title"": """"}# ""second"": ""疲乏，纳减""# ""tongue"": ""舌黯，苔白厚，中心微黄""# ""chinese"": ""黄疸""# ""therapy"": """"# ""western"": ""活动性肝炎合并肝胆道感染""# ""dialectical"": """"}"
"{""main"": ""腹部时痛，巩膜黄，小便黄，大便有时结硬""# ""pulse"": ""脉滑""# ""recipe"": {""raw

"{""main"": ""下肢遍布紫癜 牙龈亦渗血 经行量多""# ""pulse"": ""脉弦微数""# ""recipe"": {""raw"": ""旱莲草 20 g\r\n女贞子 20 g\r\n生地黄 15 g\r\n枸杞子 15 g\r\n生地榆 20 g\r\n甘草 3 g""# ""item"": [{""name"": ""旱莲草""# ""unit"": ""g""# ""amount"": ""20""}# {""name"": ""女贞子""# ""unit"": ""g""# ""amount"": ""20""}# {""name"": ""生地黄""# ""unit"": ""g""# ""amount"": ""15""}# {""name"": ""枸杞子""# ""unit"": ""g""# ""amount"": ""15""}# {""name"": ""生地榆""# ""unit"": ""g""# ""amount"": ""20""}# {""name"": ""甘草""# ""unit"": ""g""# ""amount"": ""3""}]# ""memo"": """"# ""type"": ""soup""# ""title"": ""二至丸""}# ""second"": ""头眩、口干、失眠""# ""tongue"": ""舌质红""# ""chinese"": """"# ""therapy"": ""养阴清热、凉血止血""# ""western"": ""血小板减少性紫癜""# ""dialectical"": ""阴虚内热#，血热妄行证""}"
"{""main"": ""骨痛抽掣，剧烈难忍，不能行动，面色萎黄""# ""pulse"": ""脉弦""# ""recipe"": {""raw"": ""丹参 15 克\r\n赤芍 15 克\r\n白芍 15 克\r\n陈胆星 5 克\r\n鸡血藤 30 克\r\n炒桑枝 12 克\r\n制狗脊 15 克\r\n炒川断 15 克\r\n补骨脂 9 克\r\n川石斛 9 克\r\n白英 15 克\r\n桃仁 9 克\r\n香谷芽 12 克\r\n白花蛇舌草 30 克\r\n徐长卿 15 克""# ""item"": [{""name"": ""丹参

...

"{""main"": ""背脊冰冷，口干不饮水，人水即胀，稍吃胃胀""# ""pulse"": ""脉来弦缓""# ""recipe"": {""raw"": ""制川附子 9 克 先煎\r\n带皮苓 18 克\r\n生牡蛎 30 克 先煎\r\n泽泻 9 克\r\n苍术 9 克\r\n厚朴 6 克\r\n陈皮 6 克\r\n大腹皮 9 克\r\n白芥子 4 .5克\r\n磁石 30 克\r\n酸枣仁 12 克\r\n知母 9 克""# ""item"": [{""memo"": ""先煎""# ""name"": ""制川附子""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""带皮苓""# ""unit"": ""克""# ""amount"": ""18""}# {""memo"": ""先煎""# ""name"": ""生牡蛎""# ""unit"": ""克""# ""amount"": ""30""}# {""name"": ""泽泻""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""苍术""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""厚朴""# ""unit"": ""克""# ""amount"": ""6""}# {""name"": ""陈皮""# ""unit"": ""克""# ""amount"": ""6""}# {""name"": ""大腹皮""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""白芥子""# ""unit"": "".5克""# ""amount"": ""4""}# {""name"": ""磁石""# ""unit"": ""克""# ""amount"": ""30""}# {""name"": ""酸枣仁""# ""unit"": ""克""# ""amount"": ""12""}# {""name"": ""知母""# ""unit"": ""克""# ""amount"": ""9""}]# ""memo"": """"# ""type"": ""soup""# ""title""

"{""main"": ""低烧三年""# ""pulse"": ""脉细而稍数，左关稍弦""# ""recipe"": {""raw"": ""生地黄 24 克\r\n山萸肉 12 克\r\n怀山药 12 克\r\n丹皮 12 克\r\n泽泻 9 克\r\n获苓 9 克\r\n柴胡 9 克\r\n五味子 6 克\r\n白芍 9 克\r\n紫肉桂 6 克""# ""item"": [{""name"": ""生地黄""# ""unit"": ""克""# ""amount"": ""24""}# {""name"": ""山萸肉""# ""unit"": ""克""# ""amount"": ""12""}# {""name"": ""怀山药""# ""unit"": ""克""# ""amount"": ""12""}# {""name"": ""丹皮""# ""unit"": ""克""# ""amount"": ""12""}# {""name"": ""泽泻""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""获苓""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""柴胡""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""五味子""# ""unit"": ""克""# ""amount"": ""6""}# {""name"": ""白芍""# ""unit"": ""克""# ""amount"": ""9""}# {""name"": ""紫肉桂""# ""unit"": ""克""# ""amount"": ""6""}]# ""memo"": """"# ""type"": ""soup""# ""title"": ""都气丸加柴芍桂""}# ""second"": ""夜间两腿发麻，精神委顿不振""# ""tongue"": ""舌无苔略红""# ""chinese"": ""低烧""# ""therapy"": ""滋肾调肝""# ""western"": """"# ""dialectical"": ""阴虚肝阳旺""}"
"{""main"": ""胃脘隐痛，痛时喜按，得温痛减，口

"{""main"": ""面色萎黄而浮，食后脘胀，大便溏薄，入暮足肿""# ""pulse"": ""脉象细软""# ""recipe"": {""raw"": ""熟附子 9 g\r\n肉桂 3 g 后下\r\n怀山药 30 g\r\n潞党参 12 g\r\n补骨脂 10 g\r\n桑寄生 30 g\r\n六月雪 30 g\r\n玉米须 30 g\r\n益母草 90 g 煎汤代水煎药""# ""item"": [{""name"": ""熟附子""# ""unit"": ""g""# ""amount"": ""9""}# {""memo"": ""后下""# ""name"": ""肉桂""# ""unit"": ""g""# ""amount"": ""3""}# {""name"": ""怀山药""# ""unit"": ""g""# ""amount"": ""30""}# {""name"": ""潞党参""# ""unit"": ""g""# ""amount"": ""12""}# {""name"": ""补骨脂""# ""unit"": ""g""# ""amount"": ""10""}# {""name"": ""桑寄生""# ""unit"": ""g""# ""amount"": ""30""}# {""name"": ""六月雪""# ""unit"": ""g""# ""amount"": ""30""}# {""name"": ""玉米须""# ""unit"": ""g""# ""amount"": ""30""}# {""memo"": ""煎汤代水煎药""# ""name"": ""益母草""# ""unit"": ""g""# ""amount"": ""90""}]# ""memo"": """"# ""type"": ""soup""# ""title"": """"}# ""second"": ""神疲肢乏，口干尿少，易于感冒""# ""tongue"": ""苔薄，舌淡尖红""# ""chinese"": """"# ""therapy"": ""温补脾肾，清利泄浊""# ""western"": ""慢性肾炎""# ""dialectical"": ""脾肾阳虚，湿热羁留""}"
"{""main"": ""胸闷

"{""main"": ""腹泻，便红白粘液，腹痛，里急后重""# ""pulse"": ""脉沉细滑数""# ""recipe"": {""raw"": ""白头翁 10 克\r\n黄连 5 克\r\n黄柏 3 克\r\n秦皮 3 克\r\n甘草 10 克\r\n阿胶 10 克 烊化""# ""item"": [{""name"": ""白头翁""# ""unit"": ""克""# ""amount"": ""10""}# {""name"": ""黄连""# ""unit"": ""克""# ""amount"": ""5""}# {""name"": ""黄柏""# ""unit"": ""克""# ""amount"": ""3""}# {""name"": ""秦皮""# ""unit"": ""克""# ""amount"": ""3""}# {""name"": ""甘草""# ""unit"": ""克""# ""amount"": ""10""}# {""memo"": ""烊化""# ""name"": ""阿胶""# ""unit"": ""克""# ""amount"": ""10""}]# ""memo"": """"# ""type"": ""soup""# ""title"": ""白头翁加甘草阿胶汤""}# ""second"": ""恶心，纳少乏味，发冷溲黄""# ""tongue"": ""苔薄白，舌质红""# ""chinese"": ""下利脓血""# ""therapy"": ""清热凉血，祛湿导滞""# ""western"": """"# ""dialectical"": ""湿热滞下，伤及血分""}"
"{""main"": ""恶心纳差，心下痞满，腹鸣便溏""# ""pulse"": ""脉细弱""# ""recipe"": {""raw"": ""半夏 12 克\r\n党参 10 克\r\n黄芩 10 克\r\n黄连 6 克\r\n干姜 10 克\r\n大枣 4 枚\r\n炙甘草 6 克\r\n生石膏 45 克""# ""item"": [{""name"": ""半夏""# ""unit"": ""克""# ""amount"": ""12""}# {""name"": ""党参""# ""unit"": ""

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [5]:
data = []

for i, doc in enumerate(docs):
    tokens = [t for t, label in doc]
    tagged = nltk.pos_tag(tokens)
    data.append([(w, pos, label) for (w, label), (word, pos) in zip(doc, tagged)])

print(data[0])

[('李', 'JJ', 'O'), ('某', 'NNP', 'O'), ('，', 'NNP', 'O'), ('女', 'NNP', 'O'), ('，', 'VBD', 'O'), ('6', 'CD', 'O'), ('7', 'CD', 'O'), ('岁', 'NN', 'O'), ('。', 'NNP', 'O'), ('每', 'NNP', 'O'), ('于', 'NNP', 'O'), ('夏', 'NNP', 'O'), ('日', 'NNP', 'O'), ('洗', 'NNP', 'O'), ('澡', 'NNP', 'O'), ('后', 'NNP', 'O'), ('即', 'NNP', 'O'), ('寒', 'NNP', 'B-S'), ('热', 'NNP', 'I-S'), ('不', 'NNP', 'I-S'), ('适', 'NNP', 'E-S'), ('，', 'NNP', 'O'), ('自', 'NNP', 'O'), ('感', 'NNP', 'O'), ('发', 'NNP', 'O'), ('热', 'NNP', 'O'), ('而', 'NNP', 'O'), ('又', 'NNP', 'O'), ('需', 'NNP', 'O'), ('披', 'NNP', 'O'), ('衣', 'NNP', 'O'), ('裹', 'NNP', 'O'), ('护', 'NNP', 'O'), ('。', 'NNP', 'O'), ('并', 'NNP', 'O'), ('于', 'NNP', 'O'), ('不', 'NNP', 'O'), ('知', 'NNP', 'O'), ('不', 'NNP', 'O'), ('觉', 'NNP', 'O'), ('中', 'NNP', 'O'), ('汗', 'NNP', 'B-S'), ('透', 'NNP', 'I-S'), ('衣', 'NNP', 'I-S'), ('服', 'NNP', 'E-S'), ('，', 'NNP', 'O'), ('急', 'NNP', 'O'), ('又', 'NNP', 'O'), ('换', 'NNP', 'O'), ('衣', 'NNP', 'O'), ('，', 'NNP', 'O'), ('如', 'NNP', 'O'),

In [6]:
def word2features(doc, i):
    word = doc[i][0]
    postag = doc[i][1]

    # Common features for all words
    features = [
        'bias',
        'word.lower=' + word.lower(),
        'word[-3:]=' + word[-3:],
        'word[-2:]=' + word[-2:],
        'word.isupper=%s' % word.isupper(),
        'word.istitle=%s' % word.istitle(),
        'word.isdigit=%s' % word.isdigit(),
        'postag=' + postag
    ]

    # Features for words that are not
    # at the beginning of a document
    if i > 0:
        word1 = doc[i-1][0]
        postag1 = doc[i-1][1]
        features.extend([
            '-1:word.lower=' + word1.lower(),
            '-1:word.istitle=%s' % word1.istitle(),
            '-1:word.isupper=%s' % word1.isupper(),
            '-1:word.isdigit=%s' % word1.isdigit(),
            '-1:postag=' + postag1
        ])
    else:
        # Indicate that it is the 'beginning of a document'
        features.append('BOS')

    # Features for words that are not
    # at the end of a document
    if i < len(doc)-1:
        word1 = doc[i+1][0]
        postag1 = doc[i+1][1]
        features.extend([
            '+1:word.lower=' + word1.lower(),
            '+1:word.istitle=%s' % word1.istitle(),
            '+1:word.isupper=%s' % word1.isupper(),
            '+1:word.isdigit=%s' % word1.isdigit(),
            '+1:postag=' + postag1
        ])
    else:
        # Indicate that it is the 'end of a document'
        features.append('EOS')

    return features

In [7]:
from sklearn.model_selection import train_test_split

# A function for extracting features in documents
def extract_features(doc):
    return [word2features(doc, i) for i in range(len(doc))]

# A function fo generating the list of labels for each document
def get_labels(doc):
    return [label for (token, postag, label) in doc]

X = [extract_features(doc) for doc in data]
y = [get_labels(doc) for doc in data]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)

In [8]:
print(len(X_train[0][4]))
print(X_train[0][5])

18
['bias', 'word.lower=5', 'word[-3:]=5', 'word[-2:]=5', 'word.isupper=False', 'word.istitle=False', 'word.isdigit=True', 'postag=CD', '-1:word.lower=，', '-1:word.istitle=False', '-1:word.isupper=False', '-1:word.isdigit=False', '-1:postag=VBD', '+1:word.lower=3', '+1:word.istitle=False', '+1:word.isupper=False', '+1:word.isdigit=True', '+1:postag=CD']


In [9]:
import pycrfsuite
trainer = pycrfsuite.Trainer(verbose=True)

# Submit training data to the trainer
for xseq, yseq in zip(X_train, y_train):
    trainer.append(xseq, yseq)

# Set the parameters of the model
trainer.set_params({
    # coefficient for L1 penalty
    'c1': 0.1,

    # coefficient for L2 penalty
    'c2': 0.01,  

    # maximum number of iterations
    'max_iterations': 200,

    # whether to include transitions that
    # are possible, but not observed
    'feature.possible_transitions': True
})

# Provide a file name as a parameter to the train function, such that
# the model will be saved to the file when training is finished
trainer.train('crf.model')

Feature generation
type: CRF1d
feature.minfreq: 0.000000
feature.possible_states: 0
feature.possible_transitions: 1
0....1....2....3....4....5....6....7....8....9....10
Number of features: 29911
Seconds required: 2.948

L-BFGS optimization
c1: 0.100000
c2: 0.010000
num_memories: 6
max_iterations: 200
epsilon: 0.000010
stop: 10
delta: 0.000010
linesearch: MoreThuente
linesearch.max_iterations: 20

***** Iteration #1 *****
Loss: 205321.726834
Feature norm: 1.000000
Error norm: 99981.011282
Active features: 29795
Line search trials: 1
Line search step: 0.000000
Seconds required for this iteration: 1.104

***** Iteration #2 *****
Loss: 202873.727444
Feature norm: 1.019647
Error norm: 83066.787835
Active features: 28634
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.555

***** Iteration #3 *****
Loss: 194503.010290
Feature norm: 1.111554
Error norm: 50974.160090
Active features: 22439
Line search trials: 1
Line search step: 1.000000
Seconds required 

***** Iteration #41 *****
Loss: 43792.089110
Feature norm: 21.801779
Error norm: 38303.786645
Active features: 25832
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.558

***** Iteration #42 *****
Loss: 43250.584474
Feature norm: 22.198263
Error norm: 37893.899524
Active features: 25749
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.554

***** Iteration #43 *****
Loss: 42502.971731
Feature norm: 22.428339
Error norm: 32075.197091
Active features: 25678
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.555

***** Iteration #44 *****
Loss: 42013.059031
Feature norm: 22.655712
Error norm: 35402.315474
Active features: 25614
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.559

***** Iteration #45 *****
Loss: 41375.792348
Feature norm: 22.957386
Error norm: 30528.146808
Active features: 25549
Line search trials: 1
Line search step: 1.0

***** Iteration #83 *****
Loss: 25873.737971
Feature norm: 65.395071
Error norm: 3312.285841
Active features: 21718
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.556

***** Iteration #84 *****
Loss: 25775.835382
Feature norm: 66.273040
Error norm: 5766.842202
Active features: 21821
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.552

***** Iteration #85 *****
Loss: 25682.970532
Feature norm: 67.260030
Error norm: 519.816733
Active features: 21813
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.562

***** Iteration #86 *****
Loss: 25551.525649
Feature norm: 68.971193
Error norm: 1683.761408
Active features: 21696
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.555

***** Iteration #87 *****
Loss: 25532.875950
Feature norm: 69.614747
Error norm: 12315.994600
Active features: 21692
Line search trials: 2
Line search step: 0.500000

***** Iteration #126 *****
Loss: 24383.593468
Feature norm: 86.684655
Error norm: 4559.251197
Active features: 20825
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.556

***** Iteration #127 *****
Loss: 24377.985044
Feature norm: 87.166246
Error norm: 6710.402707
Active features: 20803
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.551

***** Iteration #128 *****
Loss: 24363.023932
Feature norm: 87.362333
Error norm: 4162.221836
Active features: 20779
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.552

***** Iteration #129 *****
Loss: 24358.272299
Feature norm: 87.834692
Error norm: 6567.510102
Active features: 20785
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.551

***** Iteration #130 *****
Loss: 24344.185470
Feature norm: 88.031241
Error norm: 3901.179019
Active features: 20779
Line search trials: 1
Line search step: 1.0

***** Iteration #167 *****
Loss: 24107.980363
Feature norm: 97.679258
Error norm: 5033.815613
Active features: 20518
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.555

***** Iteration #168 *****
Loss: 24098.732362
Feature norm: 97.795760
Error norm: 2577.596204
Active features: 20509
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.554

***** Iteration #169 *****
Loss: 24096.598442
Feature norm: 98.106426
Error norm: 5229.125319
Active features: 20503
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.555

***** Iteration #170 *****
Loss: 24086.996485
Feature norm: 98.223452
Error norm: 2615.269804
Active features: 20516
Line search trials: 1
Line search step: 1.000000
Seconds required for this iteration: 0.572

***** Iteration #171 *****
Loss: 24085.264783
Feature norm: 98.527188
Error norm: 5187.440482
Active features: 20491
Line search trials: 1
Line search step: 1.0

In [10]:
tagger = pycrfsuite.Tagger()
tagger.open('crf.model')
y_pred = [tagger.tag(xseq) for xseq in X_test]

# Let's take a look at a random sample in the testing set
i = 12
for x, y in zip(y_pred[i], [x[1].split("=")[1] for x in X_test[i]]):
    print("%s (%s)" % (y, x))

初 (O)
诊 (O)
： (O)
2 (O)
0 (O)
0 (O)
6 (O)
年 (O)
1 (O)
1 (O)
月 (O)
1 (O)
1 (O)
日 (O)
。 (O)
李 (O)
某 (O)
， (O)
3 (O)
2 (O)
岁 (O)
， (O)
1 (O)
0 (O)
月 (O)
2 (O)
2 (O)
日 (O)
妊 (O)
娠 (O)
4 (O)
3 (O)
天 (O)
发 (O)
生 (O)
自 (O)
然 (O)
流 (O)
产 (O)
后 (O)
， (O)
阴 (O)
道 (O)
少 (O)
量 (O)
出 (O)
血 (O)
， (O)
色 (O)
淡 (O)
红 (O)
， (O)
至 (O)
今 (O)
未 (O)
净 (O)
， (O)
夹 (O)
带 (O)
， (O)
伴 (O)
小 (O)
腹 (O)
隐 (O)
痛 (O)
， (O)
腰 (B-S)
痛 (E-S)
， (O)
b (O)
超 (O)
检 (O)
查 (O)
未 (O)
发 (O)
现 (O)
异 (O)
常 (O)
。 (O)
血 (O)
β (O)
- (O)
绒 (O)
毛 (O)
膜 (O)
促 (O)
性 (O)
腺 (O)
激 (O)
素 (O)
测 (O)
定 (O)
： (O)
7 (O)
2 (O)
i (O)
u (O)
/ (O)
l (O)
， (O)
纳 (O)
可 (O)
， (O)
二 (O)
便 (O)
正 (O)
常 (O)
。 (O)
1 (O)
0 (O)
月 (O)
2 (O)
7 (O)
日 (O)
曾 (O)
服 (O)
生 (O)
化 (O)
汤 (O)
（ (O)
《 (O)
胎 (O)
产 (O)
秘 (O)
书 (O)
》 (O)
） (O)
加 (O)
减 (O)
4 (O)
剂 (O)
无 (O)
效 (O)
。 (O)
舌 (O)
淡 (O)
红 (O)
， (O)
苔 (O)
薄 (O)
白 (O)
， (O)
脉 (O)
细 (O)
。 (O)
治 (O)
法 (O)
： (O)
清 (O)
理 (O)
湿 (O)
热 (O)
， (O)
止 (O)
血 (O)
。 (O)
方 (O)
剂 (O)
： (O)
紫 (O)
参 (O)
汤 (O)
加 (O)
味 (O)
。 (O)
紫 (O)


In [11]:
from sklearn.metrics import accuracy_score

# Convert the sequences of tags into a 1-dimensional array
#predictions = np.array([labels[tag] for row in y_pred for tag in row])
#truths = np.array([labels[tag] for row in y_test for tag in row])

print(y_pred)

#print(accuracy_score(y_test, y_pred))

[['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-S', 'I-S', 'I-S', 'I-S', 'I-S', 'E-S', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'], ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O',

In [12]:
from sklearn.metrics import classification_report

# Create a mapping of labels to indices
labels = {"O": 0,"B-S": 1,"I-S": 2,"E-S": 3}

# Convert the sequences of tags into a 1-dimensional array
predictions = np.array([labels[tag] for row in y_pred for tag in row])
truths = np.array([labels[tag] for row in y_test for tag in row])

# Print out the classification report
print(classification_report(
    truths, predictions,
    target_names=["O", "B-S","I-S","E-S"]))

             precision    recall  f1-score   support

          O       0.98      0.99      0.99    331901
        B-S       0.49      0.19      0.27      2565
        I-S       0.42      0.19      0.26      3944
        E-S       0.50      0.19      0.28      2557

avg / total       0.96      0.97      0.97    340967

